In [37]:
import pandas as pd
from selenium import webdriver
from webdriver_manager.chrome import ChromeDriverManager
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.common.by import By
from bs4 import BeautifulSoup
import time
import sqlalchemy
from sqlalchemy import create_engine


In [38]:
# login
def login(driver, instahandle, instapassword):
    username = driver.find_element(By.CSS_SELECTOR, "input[name='username']")
    password = driver.find_element(By.CSS_SELECTOR, "input[name='password']")
    username.clear()
    password.clear()
    username.send_keys(instahandle)
    password.send_keys(instapassword)
    driver.find_element(By.CSS_SELECTOR, "button[type='submit']").click()
    time.sleep(5)
    return True

In [39]:
def skip_login_info(driver):
    #save your login info?
    time.sleep(10)
    notnow = driver.find_element("xpath", "//button[contains(text(), 'Not Now')]").click()
def turn_off_notif(driver):
    #turn on notif
    time.sleep(10)
    notnow2 = driver.find_element("xpath", "//button[contains(text(), 'Not Now')]").click()

In [40]:
#searchbox
def search(driver, instapage):
    time.sleep(5)
    searchbox = driver.find_element(By.CSS_SELECTOR, "input[placeholder='Search']")
    searchbox.clear()
    searchbox.send_keys(instapage)
    time.sleep(5)
    #selects the item
    searchbox.send_keys(Keys.ENTER);
    time.sleep(5)
    #clicks enter
    searchbox.send_keys(Keys.ENTER)

In [41]:
def set_window_size(driver):
    time.sleep(5)
    a=driver.get_window_size()
    driver.set_window_size(a["width"], a["height"])

In [42]:
def scroller(driver):
    #scroll
    time.sleep(5)
    scrolldown = driver.execute_script(
    "window.scrollTo(0, document.body.scrollHeight);var scrolldown=document.body.scrollHeight;return scrolldown;")
    match = False
    timeout = 0
    while not match:
        last_count = scrolldown
        time.sleep(3)
        scrolldown = driver.execute_script(
        "window.scrollTo(0, document.body.scrollHeight);var scrolldown=document.body.scrollHeight;return scrolldown;")
        if last_count == scrolldown:
            match = True
        if timeout == 0:
            break
        else:
            timeout-=1


In [43]:
def insta_posts(driver, limit=10):
    posts = []
    links = driver.find_elements(By.TAG_NAME, 'a')
    for link in links[:limit]:
        post = link.get_attribute('href')
        if '/p/' in post:
            posts.append(post)
    return posts

In [44]:
def getdata(driver,posts, page="",):
    raw_data = []
    for post in posts:
        print(f"Visiting page {post}")
        driver.get(post)
        time.sleep(5)
        shortcode = driver.current_url.split("/")[-2]
        print("shortcode", shortcode)
        selector = "div._aa06"
        try:
            if driver.find_element(By.CSS_SELECTOR, selector) is not None:
                content = driver.find_elements(By.CSS_SELECTOR, selector)
                for con in content:
                    html = con.get_attribute('innerHTML')
                    with open('dummy_sec.html', 'w',encoding="utf-8") as f:
                        f.write(html)
                    soup = BeautifulSoup(html,  'html.parser')

                    for link in soup.find_all('a'):
                        raw_data.append({
                            'tag':link.text,
                            'link':link.attrs.get('href'),
                            'page':soup.find('a').attrs.get('href'),
                            'date':soup.find('time').attrs.get('datetime'),
                            'img':soup.find('img').attrs.get('src')
                        })
                    print(raw_data)
            else:
                print(f"{selector} not found")
        except Exception as e:
            print(e)
        finally:
            time.sleep(5)
    return raw_data


In [45]:
def covert_data_to_df(raw_data):
    df = pd.DataFrame(raw_data)
    df[df['tag'].str.startswith('#')]
    return df
from sqlalchemy import create_engine


#     engine = create_engine('sqlite://db.sqlite', echo=False)
#     df.to_sql('hashtags', con=engine)
    # df.to_sql()
    # conn = sqlite3.connect('test_database')
    # c = conn.cursor()
    # c.execute('CREATE TABLE IF NOT EXISTS hastags(tag,link,page,date)')
    # conn.commit()
    # df.to_sql('hashtags', conn, if_exists='replace', index = False)

In [46]:
def convert_df_to_csv(df):
    df.to_csv('hastags_rawdata1.csv', index=None)
    print('Process Completed')

**Calling functions**

In [47]:
#installing driver
mdriver = webdriver.Chrome(ChromeDriverManager().install())
mdriver.get("https://www.instagram.com/")
time.sleep(2)
insta_handle='twilightqueenbee1579'
insta_password='!$@%67'
insta_page='random_shotsbyme'
#if login successful
try:
    if login(mdriver,insta_handle,insta_password):
        print("Login successful")
        skip_login_info(mdriver)
        turn_off_notif(mdriver)
        mdriver.get("https://www.instagram.com/explore")
        set_window_size(mdriver)
        scroller(mdriver)
        time.sleep(3)
        fetched_posts=insta_posts(mdriver, 10)
        print(fetched_posts)
        print(f'len of posts {len(fetched_posts)}')
        fetched_data=getdata(mdriver,fetched_posts,insta_page)
        dataframe=covert_data_to_df(fetched_data)
        convert_df_to_csv(dataframe)
    else:
        print("Wrong credentials")
except Exception as e:
     print(e)

# mdriver.quit()



C:\Users\Ananya Misra\AppData\Local\Temp\ipykernel_10472\4146343365.py:2: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  mdriver = webdriver.Chrome(ChromeDriverManager().install())


Login successful
['https://www.instagram.com/p/CmUJAC4j2-C/', 'https://www.instagram.com/p/CmN10eJrUvz/', 'https://www.instagram.com/p/BxSTy2Epe41/', 'https://www.instagram.com/p/Cm2CQkPP25y/', 'https://www.instagram.com/p/CnP0xrIJ54h/', 'https://www.instagram.com/p/CnUvGx2u_E7/', 'https://www.instagram.com/p/CnKIaJojBDU/', 'https://www.instagram.com/p/Cgml_UdqO0K/', 'https://www.instagram.com/p/Cm2o9AbhQsd/', 'https://www.instagram.com/p/Cm7Rocjovpf/']
len of posts 10
Visiting page https://www.instagram.com/p/CmUJAC4j2-C/
shortcode CmUJAC4j2-C
[{'tag': '', 'link': '/carriemeonmyway/', 'page': '/carriemeonmyway/', 'date': '2022-12-18T15:45:48.000Z', 'img': 'https://instagram.flko11-1.fna.fbcdn.net/v/t51.2885-19/20590176_1527853053944947_2726696851569901568_a.jpg?stp=dst-jpg_s150x150&_nc_ht=instagram.flko11-1.fna.fbcdn.net&_nc_cat=107&_nc_ohc=8ceS1ZP0vvIAX9mUivV&edm=ALQROFkBAAAA&ccb=7-5&oh=00_AfD6un2YZi_fVxXXQ8R7EpdNllWVhAqaTQyH29MWDUT8Cg&oe=63C6AA3E&_nc_sid=30a2ef'}, {'tag': 'carriemeo

In [48]:
dataframe

tag                                 link  \
0                                            /carriemeonmyway/   
1         carriemeonmyway                    /carriemeonmyway/   
2                #rapanui               /explore/tags/rapanui/   
3           #easterisland          /explore/tags/easterisland/   
4           #isladepascua          /explore/tags/isladepascua/   
..                    ...                                  ...   
299          creusa._lima                       /creusa._lima/   
300                    1w  /p/Cm7Rocjovpf/c/17972789656894413/   
301                                     /lorenalorenalorena77/   
302  lorenalorenalorena77               /lorenalorenalorena77/   
303                    2d  /p/Cm7Rocjovpf/c/17974208410992200/   

                       page                      date  \
0         /carriemeonmyway/  2022-12-18T15:45:48.000Z   
1         /carriemeonmyway/  2022-12-18T15:45:48.000Z   
2         /carriemeonmyway/  2022-12-18T15:45:48.000Z   
3         /carriemeonmyway/  2022-12-18T15:45:48.000Z   
4         /carriemeonmyway/  2022-12-18T15:45:48.000Z   
..                      ...                       ...   
299          /creusa._lima/  2023-01-06T17:24:04.000Z   
300          /creusa._lima/  2023-01-06T17:24:04.000Z   
301  /lorenalorenalorena77/  2023-01-11T20:29:52.000Z   
302  /lorenalorenalorena77/  2023-01-11T20:29:52.000Z   
303  /lorenalorenalorena77/  2023-01-11T20:29:52.000Z   

                                                   img  
0    https://instagram.flko11-1.fna.fbcdn.net/v/t51...  
1    https://instagram.flko11-1.fna.fbcdn.net/v/t51...  
2    https://instagram.flko11-1.fna.fbcdn.net/v/t51...  
3    https://instagram.flko11-1.fna.fbcdn.net/v/t51...  
4    https://instagram.flko11-1.fna.fbcdn.net/v/t51...  
..                                                 ...  
299  https://instagram.flko11-1.fna.fbcdn.net/v/t51...  
300  https://instagram.flko11-1.fna.fbcdn.net/v/t51...  
301  https://instagram.flko11-1.fna.fbcdn.net/v/t51...  
302  https://instagram.flko11-1.fna.fbcdn.net/v/t51...  
303  https://instagram.flko11-1.fna.fbcdn.net/v/t51...  

[304 rows x 5 columns]

In [51]:
dataframe.img[0]

'https://instagram.flko11-1.fna.fbcdn.net/v/t51.2885-19/20590176_1527853053944947_2726696851569901568_a.jpg?stp=dst-jpg_s150x150&_nc_ht=instagram.flko11-1.fna.fbcdn.net&_nc_cat=107&_nc_ohc=8ceS1ZP0vvIAX9mUivV&edm=ALQROFkBAAAA&ccb=7-5&oh=00_AfD6un2YZi_fVxXXQ8R7EpdNllWVhAqaTQyH29MWDUT8Cg&oe=63C6AA3E&_nc_sid=30a2ef'

In [49]:
#filtering the dataframe on the basis of #
mask = dataframe['tag'].str.contains('#', case=False, na=False)
new_dataframe=dataframe[mask]
#converting the new dataframe to csv
new_dataframe
new_dataframe.sort_values('1')


KeyError: '1'

In [ ]:
convert_df_to_csv(new_dataframe)

In [ ]:
def save_dataframe(df:pd.DataFrame):
    from datetime import datetime
    val = datetime.now().strftime("_%d_%m_%y")
    engine = create_engine('sqlite:///hashtags.sqlite3', echo=False)
    df.to_sql(f'hashtag_{val}', con=engine, if_exists='append')



In [ ]:
datetime.now()save_dataframe(new_dataframe)

*this command is not running: python3 -m venv env
red line in line 94*

In [ ]:
from datetime import datetime
value = datetime.now().strftime("_%d_%m_%y")
print(value)